In [1]:
import gym
import numpy as np
rm='Pong-v4'

In [2]:
%matplotlib inline
from matplotlib import animation
import matplotlib.pyplot as plt
from IPython.display import display, HTML

def display_frames_as_gif(frames):
    plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 144)
    patch = plt.imshow(frames[0])
    plt.axis('off')
    def animate(i):
        patch.set_data(frames[i])
    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=50)
    plt.close(anim._fig)
    display(HTML(anim.to_jshtml()))

In [3]:
from gym.wrappers import AtariPreprocessing
gym.new_step_api=True
env = gym.make(rm)
# model initialization
H = 200 # number of hidden layer neurons
D = 80 * 80 # input dimensionality: 80x80 grid
model = {}
model['W1'] = np.random.randn(H,D) / np.sqrt(D) # "Xavier" initialization
model['W2'] = np.random.randn(H) / np.sqrt(H)
# hyperparameters
batch_size = 10 # every how many episodes to do a param update?
learning_rate = 1e-3
#learning_rate = 1e-3
gamma = 0.99 # discount factor for reward
decay_rate = 0.99 # decay factor for RMSProp leaky sum of grad^2
grad_buffer = { k : np.zeros_like(v) for k,v in model.items() } # update buffers that add up gradients over a batch
rmsprop_cache = { k : np.zeros_like(v) for k,v in model.items() } # rmsprop memory

def sigmoid(x): 
  return 1.0 / (1.0 + np.exp(-x)) # sigmoid "squashing" function to interval [0,1]

def prepro(I):
  """ prepro 210x160x3 uint8 frame into 6400 (80x80) 1D float vector """
  I=np.asarray(I)
  I = I[35:195] # crop
  
  I = I[::2,::2,0] # downsample by factor of 2
  
  I[I == 144] = 0 # erase background (background type 1)
  
  I[I == 109] = 0 # erase background (background type 2)
  
  I[I != 0] = 1 # everything else (paddles, ball) just set to 1
  return I.astype(float).ravel()

def discount_rewards(r):
  """ take 1D float array of rewards and compute discounted reward """
  discounted_r = np.zeros_like(r)
  running_add = 0
  for t in reversed(range(0, r.size)):
    if r[t] != 0: running_add = 0 # reset the sum, since this was a game boundary (pong specific!)
    running_add = running_add * gamma + r[t]
    discounted_r[t] = running_add
  return discounted_r

def policy_forward(x):
  h = np.dot(model['W1'], x)
  h[h<0] = 0 # ReLU nonlinearity
  logp = np.dot(model['W2'], h)
  p = sigmoid(logp)
  return p, h # return probability of taking action 2, and hidden state

def policy_backward(epx, eph, epdlogp):
  """ backward pass. (eph is array of intermediate hidden states) """
  dW2 = np.dot(eph.T, epdlogp).ravel()
  dh = np.outer(epdlogp, model['W2'])
  dh[eph <= 0] = 0 # backpro prelu
  dW1 = np.dot(dh.T, epx)
  return {'W1':dW1, 'W2':dW2}

def model_step(model, observation, prev_x):
  # preprocess the observation, set input to network to be difference image
  cur_x = prepro(observation)
  x = cur_x - prev_x if prev_x is not None else np.zeros(D)
  prev_x = cur_x
  
  # forward the policy network and sample an action from the returned probability
  aprob, _ = policy_forward(x)
  action = 2 if aprob >= 0.5 else 3 # roll the dice!
  
  return action, prev_x

def play_game(env, model):
  observation = env.reset()

  frames = []
  cumulated_reward = 0

  prev_x = None # used in computing the difference frame

  for t in range(1000):
      frames.append(env.render(mode = 'rgb_array'))
      action, prev_x = model_step(model, observation, prev_x)
      observation, reward, done, info = env.step(action)
      cumulated_reward += reward
      if done:
          print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
          break
  print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))
  env.close()
  display_frames_as_gif(frames)

def train_model(env, model, total_episodes = 100):
  hist = []
  observation = env.reset()

  prev_x = None # used in computing the difference frame
  xs,hs,dlogps,drs = [],[],[],[]
  running_reward = None
  reward_sum = 0
  episode_number = 0

  while True:
    # preprocess the observation, set input to network to be difference image
    cur_x = prepro(observation)
    x = cur_x - prev_x if prev_x is not None else np.zeros(D)
    prev_x = cur_x

    # forward the policy network and sample an action from the returned probability
    aprob, h = policy_forward(x)
    action = 2 if np.random.uniform() < aprob else 3 # roll the dice!

    # record various intermediates (needed later for backprop)
    xs.append(x) # observation
    hs.append(h) # hidden state
    y = 1 if action == 2 else 0 # a "fake label"
    dlogps.append(y - aprob) # grad that encourages the action that was taken to be taken (see http://cs231n.github.io/neural-networks-2/#losses if confused)

    # step the environment and get new measurements
    observation, reward, done, info = env.step(action)
    reward_sum += reward

    drs.append(reward) # record reward (has to be done after we call step() to get reward for previous action)

    if done: # an episode finished
      episode_number += 1

      # stack together all inputs, hidden states, action gradients, and rewards for this episode
      epx = np.vstack(xs)
      eph = np.vstack(hs)
      epdlogp = np.vstack(dlogps)
      epr = np.vstack(drs)
      xs,hs,dlogps,drs = [],[],[],[] # reset array memory

      # compute the discounted reward backwards through time
      discounted_epr = discount_rewards(epr)
      # standardize the rewards to be unit normal (helps control the gradient estimator variance)
      discounted_epr -= np.mean(discounted_epr)
      discounted_epr /= np.std(discounted_epr)

      epdlogp *= discounted_epr # modulate the gradient with advantage (PG magic happens right here.)
      grad = policy_backward(epx, eph, epdlogp)
      for k in model: grad_buffer[k] += grad[k] # accumulate grad over batch

      # perform rmsprop parameter update every batch_size episodes
      if episode_number % batch_size == 0:
        for k,v in model.items():
          g = grad_buffer[k] # gradient
          rmsprop_cache[k] = decay_rate * rmsprop_cache[k] + (1 - decay_rate) * g**2
          model[k] += learning_rate * g / (np.sqrt(rmsprop_cache[k]) + 1e-5)
          grad_buffer[k] = np.zeros_like(v) # reset batch gradient buffer

      # boring book-keeping
      running_reward = reward_sum if running_reward is None else running_reward * 0.99 + reward_sum * 0.01
      hist.append((episode_number, reward_sum, running_reward))
      print ('episode %f, reward total was %f. running mean: %f' % (episode_number, reward_sum, running_reward))
      reward_sum = 0
      observation = env.reset() # reset env
      prev_x = None
      if episode_number == total_episodes: 
        return hist

    # if reward != 0: # Pong has either +1 or -1 reward exactly when game ends.
    #   print('ep {}: game finished, reward: {}'.format(episode_number, reward) + ('' if reward == -1 else ' !!!!!!!!'))

c:\users\administrator\appdata\local\programs\python\python38\lib\site-packages\gym\core.py:329: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
c:\users\administrator\appdata\local\programs\python\python38\lib\site-packages\gym\wrappers\step_api_compatibility.py:39: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(


In [4]:
env.action_space

Discrete(6)

In [5]:
env.unwrapped.get_action_meanings()

['NOOP', 'FIRE', 'RIGHT', 'LEFT', 'RIGHTFIRE', 'LEFTFIRE']

In [6]:
%time hist1 = train_model(env, model, total_episodes=6000)

c:\users\administrator\appdata\local\programs\python\python38\lib\site-packages\gym\utils\passive_env_checker.py:227: DeprecationWarning: WARN: Core environment is written in old step API which returns one bool instead of two. It is recommended to rewrite the environment with new step API. 
  logger.deprecation(


episode 1.000000, reward total was -21.000000. running mean: -21.000000
episode 2.000000, reward total was -21.000000. running mean: -21.000000
episode 3.000000, reward total was -20.000000. running mean: -20.990000
episode 4.000000, reward total was -19.000000. running mean: -20.970100
episode 5.000000, reward total was -21.000000. running mean: -20.970399
episode 6.000000, reward total was -20.000000. running mean: -20.960695
episode 7.000000, reward total was -21.000000. running mean: -20.961088
episode 8.000000, reward total was -21.000000. running mean: -20.961477
episode 9.000000, reward total was -21.000000. running mean: -20.961862
episode 10.000000, reward total was -21.000000. running mean: -20.962244
episode 11.000000, reward total was -19.000000. running mean: -20.942621
episode 12.000000, reward total was -20.000000. running mean: -20.933195
episode 13.000000, reward total was -21.000000. running mean: -20.933863
episode 14.000000, reward total was -21.000000. running mean

episode 114.000000, reward total was -21.000000. running mean: -20.425627
episode 115.000000, reward total was -21.000000. running mean: -20.431370
episode 116.000000, reward total was -19.000000. running mean: -20.417057
episode 117.000000, reward total was -20.000000. running mean: -20.412886
episode 118.000000, reward total was -20.000000. running mean: -20.408757
episode 119.000000, reward total was -21.000000. running mean: -20.414670
episode 120.000000, reward total was -21.000000. running mean: -20.420523
episode 121.000000, reward total was -19.000000. running mean: -20.406318
episode 122.000000, reward total was -19.000000. running mean: -20.392255
episode 123.000000, reward total was -19.000000. running mean: -20.378332
episode 124.000000, reward total was -21.000000. running mean: -20.384549
episode 125.000000, reward total was -21.000000. running mean: -20.390703
episode 126.000000, reward total was -18.000000. running mean: -20.366796
episode 127.000000, reward total was -

episode 225.000000, reward total was -19.000000. running mean: -20.124722
episode 226.000000, reward total was -21.000000. running mean: -20.133475
episode 227.000000, reward total was -17.000000. running mean: -20.102140
episode 228.000000, reward total was -18.000000. running mean: -20.081119
episode 229.000000, reward total was -20.000000. running mean: -20.080308
episode 230.000000, reward total was -19.000000. running mean: -20.069505
episode 231.000000, reward total was -20.000000. running mean: -20.068810
episode 232.000000, reward total was -20.000000. running mean: -20.068122
episode 233.000000, reward total was -20.000000. running mean: -20.067440
episode 234.000000, reward total was -20.000000. running mean: -20.066766
episode 235.000000, reward total was -19.000000. running mean: -20.056098
episode 236.000000, reward total was -21.000000. running mean: -20.065537
episode 237.000000, reward total was -18.000000. running mean: -20.044882
episode 238.000000, reward total was -

episode 336.000000, reward total was -20.000000. running mean: -19.561508
episode 337.000000, reward total was -15.000000. running mean: -19.515893
episode 338.000000, reward total was -20.000000. running mean: -19.520734
episode 339.000000, reward total was -17.000000. running mean: -19.495527
episode 340.000000, reward total was -17.000000. running mean: -19.470572
episode 341.000000, reward total was -18.000000. running mean: -19.455866
episode 342.000000, reward total was -18.000000. running mean: -19.441307
episode 343.000000, reward total was -21.000000. running mean: -19.456894
episode 344.000000, reward total was -21.000000. running mean: -19.472325
episode 345.000000, reward total was -19.000000. running mean: -19.467602
episode 346.000000, reward total was -18.000000. running mean: -19.452926
episode 347.000000, reward total was -19.000000. running mean: -19.448397
episode 348.000000, reward total was -21.000000. running mean: -19.463913
episode 349.000000, reward total was -

...

episode 5530.000000, reward total was 7.000000. running mean: 3.688934
episode 5531.000000, reward total was 7.000000. running mean: 3.722045
episode 5532.000000, reward total was 7.000000. running mean: 3.754825
episode 5533.000000, reward total was 2.000000. running mean: 3.737276
episode 5534.000000, reward total was 2.000000. running mean: 3.719904
episode 5535.000000, reward total was -3.000000. running mean: 3.652705
episode 5536.000000, reward total was 3.000000. running mean: 3.646178
episode 5537.000000, reward total was -9.000000. running mean: 3.519716
episode 5538.000000, reward total was -5.000000. running mean: 3.434519
episode 5539.000000, reward total was 5.000000. running mean: 3.450173
episode 5540.000000, reward total was 2.000000. running mean: 3.435672
episode 5541.000000, reward total was 9.000000. running mean: 3.491315
episode 5542.000000, reward total was 6.000000. running mean: 3.516402
episode 5543.000000, reward total was 9.000000. running mean: 3.571238
epi

episode 5645.000000, reward total was 12.000000. running mean: 4.010273
episode 5646.000000, reward total was 6.000000. running mean: 4.030171
episode 5647.000000, reward total was -5.000000. running mean: 3.939869
episode 5648.000000, reward total was 6.000000. running mean: 3.960470
episode 5649.000000, reward total was -2.000000. running mean: 3.900866
episode 5650.000000, reward total was -4.000000. running mean: 3.821857
episode 5651.000000, reward total was -4.000000. running mean: 3.743638
episode 5652.000000, reward total was -6.000000. running mean: 3.646202
episode 5653.000000, reward total was 7.000000. running mean: 3.679740
episode 5654.000000, reward total was 8.000000. running mean: 3.722943
episode 5655.000000, reward total was 3.000000. running mean: 3.715713
episode 5656.000000, reward total was 2.000000. running mean: 3.698556
episode 5657.000000, reward total was 4.000000. running mean: 3.701570
episode 5658.000000, reward total was 3.000000. running mean: 3.694555


episode 5760.000000, reward total was 4.000000. running mean: 4.336230
episode 5761.000000, reward total was 2.000000. running mean: 4.312867
episode 5762.000000, reward total was 14.000000. running mean: 4.409739
episode 5763.000000, reward total was -1.000000. running mean: 4.355641
episode 5764.000000, reward total was 6.000000. running mean: 4.372085
episode 5765.000000, reward total was 1.000000. running mean: 4.338364
episode 5766.000000, reward total was 7.000000. running mean: 4.364980
episode 5767.000000, reward total was -1.000000. running mean: 4.311331
episode 5768.000000, reward total was 8.000000. running mean: 4.348217
episode 5769.000000, reward total was 6.000000. running mean: 4.364735
episode 5770.000000, reward total was 7.000000. running mean: 4.391088
episode 5771.000000, reward total was 6.000000. running mean: 4.407177
episode 5772.000000, reward total was 10.000000. running mean: 4.463105
episode 5773.000000, reward total was 6.000000. running mean: 4.478474
ep

episode 5875.000000, reward total was -1.000000. running mean: 4.055041
episode 5876.000000, reward total was 6.000000. running mean: 4.074491
episode 5877.000000, reward total was 7.000000. running mean: 4.103746
episode 5878.000000, reward total was 7.000000. running mean: 4.132708
episode 5879.000000, reward total was 5.000000. running mean: 4.141381
episode 5880.000000, reward total was 9.000000. running mean: 4.189967
episode 5881.000000, reward total was 11.000000. running mean: 4.258068
episode 5882.000000, reward total was 3.000000. running mean: 4.245487
episode 5883.000000, reward total was -16.000000. running mean: 4.043032
episode 5884.000000, reward total was 18.000000. running mean: 4.182602
episode 5885.000000, reward total was 12.000000. running mean: 4.260776
episode 5886.000000, reward total was 4.000000. running mean: 4.258168
episode 5887.000000, reward total was -3.000000. running mean: 4.185586
episode 5888.000000, reward total was 10.000000. running mean: 4.24373

episode 5990.000000, reward total was 12.000000. running mean: 4.380396
episode 5991.000000, reward total was 1.000000. running mean: 4.346592
episode 5992.000000, reward total was 5.000000. running mean: 4.353126
episode 5993.000000, reward total was 4.000000. running mean: 4.349595
episode 5994.000000, reward total was 3.000000. running mean: 4.336099
episode 5995.000000, reward total was 12.000000. running mean: 4.412738
episode 5996.000000, reward total was -5.000000. running mean: 4.318611
episode 5997.000000, reward total was 3.000000. running mean: 4.305425
episode 5998.000000, reward total was 1.000000. running mean: 4.272370
episode 5999.000000, reward total was 8.000000. running mean: 4.309647
episode 6000.000000, reward total was 14.000000. running mean: 4.406550
CPU times: total: 1d 7h 29min 28s
Wall time: 1d 12h 37min 39s


In [7]:
play_game(env, model)

c:\users\administrator\appdata\local\programs\python\python38\lib\site-packages\gym\core.py:51: DeprecationWarning: WARN: The argument mode in render method is deprecated; use render_mode during environment initialization instead.
See here for more information: https://www.gymlibrary.ml/content/api/
  deprecation(
c:\users\administrator\appdata\local\programs\python\python38\lib\site-packages\gym\utils\passive_env_checker.py:297: UserWarning: WARN: No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps.
  logger.warn(


Episode finished without success, accumulated reward = 1.0
